In [1]:
import pandas as pd
from transformers import pipeline

# Crear un pipeline de análisis de sentimiento
pipe = pipeline('sentiment-analysis', model="nlptown/bert-base-multilingual-uncased-sentiment")

C:\Users\samuel\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.11_qbz5n2kfra8p0\LocalCache\local-packages\Python311\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [9]:
# Mapea los valores de sentimientos a valores numericos
mapeo_valores = {'1 star': 1, '2 stars': 2, '3 stars': 3, '4 stars': 4, '5 stars': 5}

csv_path = 'comments/gianninaazar_comments.csv'

perfil = 'gianninaazar'
data = pd.read_csv(csv_path)

data.head()


post_id         comment_id   comment_user  \
0  2196534537424940788  17902420256851211        plinia2   
1  2196534537424940788  18108958498333424        bisbies   
2  2196534537424940788  18007710172982676  john_agudeloh   
3  2196534537424940788  18053976637486239     e_jimenez_   
4  2196534537424940788  18074685025404287  masieltaveras   

                                        comment_text  
0  Omg que emoción nada más y nada menos que la d...  
1                   🙌🙌🙌🙌🙌❤️enhorabuena guapísima 🙏❤️  
2                                                🔥🔥👏  
3                                Nicely done Gina 😍👏  
4                                                  🔥

In [10]:
# Obtener la lista de comentarios y comment_ids
df_list = data['comment_text'].tolist()
comment_ids = data['comment_id'].tolist()

max_comment_length = 512
for comment_id, comment in zip(comment_ids, df_list):
        if isinstance(comment, str) and comment.strip():  # Verificar si el comentario no está vacío
            comment = comment[:max_comment_length] #truncar el comentario si es mas largo que la longitud maxima
            result = pipe(comment)

            print(f"Comment ID: {comment_id}")
            print(f"Comentario: {comment}")
            print(f"Polaridad: {result[0]['label']}, Score: {round(result[0]['score'], 4)}")
            print()

            # Agregar los resultados al DataFrame
            data.loc[data['comment_id'] == comment_id, 'sentiment_label'] = mapeo_valores[result[0]['label']]

        elif isinstance(comment, str) and not comment.strip():
            print(f"Post ID: {comment_id}")
            print("Comentario vacío. No se realiza el análisis de sentimiento.")
            print()
        else:
            print(f"Post ID: {comment_id}")
            print("Comentario no es una cadena de texto. No se realiza el análisis de sentimiento.")
            print()


Comment ID: 17902420256851211
Comentario: Omg que emoción nada más y nada menos que la dicha GWEN
Polaridad: 1 star, Score: 0.2574

Comment ID: 18108958498333424
Comentario: 🙌🙌🙌🙌🙌❤️enhorabuena guapísima 🙏❤️
Polaridad: 3 stars, Score: 0.2235

Comment ID: 18007710172982676
Comentario: 🔥🔥👏
Polaridad: 5 stars, Score: 0.3086

Comment ID: 18053976637486239
Comentario: Nicely done Gina 😍👏
Polaridad: 5 stars, Score: 0.5384

Comment ID: 18074685025404287
Comentario: 🔥
Polaridad: 5 stars, Score: 0.3086

Comment ID: 17861181995979904
Comentario: 🔥🔥🔥
Polaridad: 5 stars, Score: 0.3086

Comment ID: 18012291952882627
Comentario: La maestra que orgullo 👏👏👏👏espectacular como siempre 😍😍😍😍😍
Polaridad: 5 stars, Score: 0.8532

Comment ID: 17971059725538462
Comentario: ❤️❤️❤️❤️❤️
Polaridad: 5 stars, Score: 0.3086

Comment ID: 17993470727496732
Comentario: 🔥
Polaridad: 5 stars, Score: 0.3086

Comment ID: 17905475705764568
Comentario: Check dm ❤️😍
Polaridad: 5 stars, Score: 0.3127

Comment ID: 180055929289432

In [11]:
#  Calcular la media de los resultados por post_id
csv_sentiments = data.groupby('post_id')['sentiment_label'].mean().reset_index()

# Exportar la media de los resultados a un archivo Excel
csv_sentiments.to_csv(f'sentiments/{perfil}_sentiments.csv', index=False)

csv_sentiments


post_id  sentiment_label
0     573834423944987990         3.000000
1     577667448063509625         4.250000
2     663346641979425953         5.000000
3     841358562241398413         3.666667
4     841359674134611628         3.000000
..                   ...              ...
595  3193853186308629358         4.750000
596  3208081656669216723         5.000000
597  3208084683136285691         4.972973
598  3212254221121215170         4.750000
599  3218222996287525264         5.000000

[600 rows x 2 columns]